## Combining all downstream used A2TEA data into one RDS object
## Also performing necessary data manipulation

In [ ]:
###packages currently installed via conda

#if (!requireNamespace("BiocManager", quietly = TRUE))
#    install.packages("BiocManager")
#BiocManager::install(version = "3.12")

#BiocManager::install("DESeq2")
#BiocManager::install("ggtree")
#BiocManager::install("Biostrings")

#lfcShrinkage isn't installable at the moment - problem for later
#install.packages("mvtnorm")
#BiocManager::install("apeglm")

#install.packages("data.table")

#install.packages("seqinr")
#install.packages("VennDiagram")
#install.packages("UpSetR")
#install.packages("cowplot")
#install.packages("ggplotify")

###############################################


if (!requireNamespace("BiocManager", quietly=TRUE))
    install.packages("BiocManager")

BiocManager::install("ggtree")
BiocManager::install("ggtreeExtra")
BiocManager::install("Biostrings")

install.packages("VennDiagram")
install.packages("UpSetR")
install.packages("cowplot")
install.packages("ggplotify")

In [1]:
library(DESeq2)
#library(BiocGenerics) # comes with DESeq2
#library(apeglm) # currently difficulties with install # better DESseq2 calc; later 

library(tidyverse)
library(ggtree)
library(Biostrings)
library(seqinr)
library(VennDiagram)
library(UpSetR)
library(cowplot)
library(ggplotify)
library(ape)

Loading required package: S4Vectors

Loading required package: stats4

Loading required package: BiocGenerics

Loading required package: parallel


Attaching package: ‘BiocGenerics’


The following objects are masked from ‘package:parallel’:

    clusterApply, clusterApplyLB, clusterCall, clusterEvalQ,
    clusterExport, clusterMap, parApply, parCapply, parLapply,
    parLapplyLB, parRapply, parSapply, parSapplyLB


The following objects are masked from ‘package:stats’:

    IQR, mad, sd, var, xtabs


The following objects are masked from ‘package:base’:

    anyDuplicated, append, as.data.frame, basename, cbind, colnames,
    dirname, do.call, duplicated, eval, evalq, Filter, Find, get, grep,
    grepl, intersect, is.unsorted, lapply, Map, mapply, match, mget,
    order, paste, pmax, pmax.int, pmin, pmin.int, Position, rank,
    rbind, Reduce, rownames, sapply, setdiff, sort, table, tapply,
    union, unique, unsplit, which.max, which.min



Attaching package: ‘S4Vectors’


The follow

#### Find all DESeq2 differential expression RDS objects and load them
##### Names are given based on the species/ecotype/etc. name

In [3]:
getwd()

[1] "/scratch2/cropbio/stoecker/A2TEA-pipeline/better_calcs/a2tea/notebooks"

In [3]:
setwd("/scratch2/cropbio/stoecker/A2TEA-pipeline/better_calcs/a2tea")

dea_list <- list.files(path = "R/deseq2/dea_final/", pattern = "dea_*", full.names=TRUE)
dea_list_short <- list.files(path = "R/deseq2/dea_final/", pattern = "dea_*", full.names=FALSE)

listRDS <- lapply(dea_list, readRDS, .GlobalEnv)

for (i in 1:length(listRDS)){
    assign(str_sub(dea_list_short[[i]], start=5), listRDS[[i]])
}

# remove unused combined list object
rm(listRDS)

In [ ]:
#nice for later - but needs install of package "apeglm"

#link on logFC shrinking
#https://support.bioconductor.org/p/77461/
#?lfcShrink
#lfcShrink(arabidopsis_dea, coef=2, type="apeglm")
#resultsNames(arabidopsis_dea)

In [ ]:
# DESeq2 testing
#At <- readRDS("R/deseq2/dea_final/dea_Arabidopsis_thaliana")
#DESeq2::results(At)
#as.data.frame(results(Arabidopsis_thaliana))

In [4]:
species_list <- vector()

for (i in 1:length(dea_list_short)){
    species_list <- c(species_list, str_sub(dea_list_short[[i]], start=5))
}

list_AllSpeciesDEResultsDataFrames <- list()

for (i in species_list) {
    # individual species file could be deleted but perhaps I'll need them later; kept for now...
    assign(paste0(i, "_DEresultsTable"), as.data.frame(results(get(i))))
    # create gene name vector here (when list is constructed rownames become unique species-gene combination)
    gene <- rownames(get(paste0(i, "_DEresultsTable")))
    df_with_genes <- add_column(get(paste0(i, "_DEresultsTable")), gene, .before = "baseMean")
    # also add a species column which will will also come in handy during the shiny steps
    species <- replicate(nrow(df_with_genes), i)
    df_with_genes <- add_column(df_with_genes, species, .before = "gene")
    # create list of dataframes, which will come in handy
    list_AllSpeciesDEResultsDataFrames[[i]] <- df_with_genes
    # list_AllSpeciesDEResultsDataFrames[[i]] <- (get(paste0(i, "_DEresultsTable")))
}

#str(list_AllSpeciesDEResultsDataFrames)

#create combined "mega" dataframe of all species, which is going  to be used for shiny lookup

combined_AllSpeciesDEResultsDataFrames <- do.call("rbind", list_AllSpeciesDEResultsDataFrames)


#str(combined_AllSpeciesDEResultsDataFrames)
#head(combined_AllSpeciesDEResultsDataFrames)
#head(list_AllSpeciesDEResultsDataFrames[[1]])
#?rbind

### creating long format HOG-genes relation table

In [5]:
HOG_file_raw <- read_delim("orthofinder/final-results/Phylogenetic_Hierarchical_Orthogroups/N0.tsv", delim = "\t")

#drop the OG, Gene Tree Parent Clade
HOG_file_short <- HOG_file_raw %>% select (-c(OG, `Gene Tree Parent Clade`)) 


#merge all species columns into one and remove the solo ones
#use all colnames except first - thus all species
HOG_file_merged <- HOG_file_short %>% unite(x,
                                          c(colnames(HOG_file_short)[-1]),
                                          sep = ",", 
                                          na.rm = TRUE,
                                          remove = TRUE)

#transform into long format - each row 1 gene and it's corresponding HOG in seperate columns
HOG_file_long <- HOG_file_merged %>%
                    mutate(unpacked = str_split(x, ",")) %>%
                    unnest(cols = c(unpacked)) %>%
                    mutate(genes = str_trim(unpacked)) %>% 
                    select(-c(x, unpacked)) %>% 
                    rename(gene = genes)

str(HOG_file_long)


── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  HOG = col_character(),
  OG = col_character(),
  `Gene Tree Parent Clade` = col_character(),
  Arabidopsis_thaliana = col_character(),
  Hordeum_vulgare = col_character(),
  Zea_mays = col_character()
)




tibble [91,542 × 2] (S3: tbl_df/tbl/data.frame)
 $ HOG : chr [1:91542] "N0.HOG0000000" "N0.HOG0000000" "N0.HOG0000000" "N0.HOG0000000" ...
 $ gene: chr [1:91542] "Zm00001d049811" "Zm00001d010350" "Zm00001d012872" "Zm00001d023233" ...


### adding specific HOG or singleton info as HOG column to DE tables

In [6]:
#?full_join
HOG_DE.a2tea <- full_join(combined_AllSpeciesDEResultsDataFrames, HOG_file_long, 
              by = c("gene")) %>% 
                replace_na(list(HOG = "singleton"))

#add column for significance - default level is padj <= 0.1

#subset tidyverse with the right functions ;D
#filter(HOG_DE.a2tea, padj < 0.05)
#?drop_na

significant <- vector()
for (FDR in HOG_DE.a2tea$padj) {
    if (!is.na(FDR) && FDR < 0.1) {
        significant <- c(significant, "yes")
    }
    else if (!is.na(FDR) && FDR > 0.1) {
        significant <- c(significant, "no")
    }
    else if (is.na(FDR)) {
        significant <- c(significant, "no")
    }
}

HOG_DE.a2tea <- add_column(HOG_DE.a2tea, significant, .after = "padj")

In [ ]:
#

### load in the rest of the data - hypotheses, trees, fasta and msa for the start 
### + toDo general stats, especially once Orthofinder calculates for HOG)
### +toDo Venn DIagrammes (until 5 species or so then alternative plots)

In [7]:
#extended_BLAST_hits <- readRDS("tea/2/extended_BLAST_hits/extended_BLAST_hits.RDS")
setClass("extended_BLAST_hits", 
         slots=list(blast_table="tbl_df",
                    num_genes_HOG="numeric",
                    num_genes_extend="numeric",
                    num_genes_complete="numeric",
                    genes_HOG="tbl_df",
                    genes_extend_hits="tbl_df")
         )
#expanded_OGs_short
#extended_BLAST_hits[["N0.HOG0000207"]]@nrow_table

In [ ]:
#readAAStringSet(paste0("tea/", 1, "/muscle/", "N0.HOG0000207", ".afa"))

In [ ]:
hypotheses

In [8]:
hypotheses <- as.data.frame(
                t(
                  read.table("config/hypotheses.tsv",
                             header = FALSE,
                             sep = "\t",
                             row.names = NULL)
                )
              )
# first line as header/column names
names(hypotheses) <- hypotheses[1,]
# delete first line
hypotheses <- hypotheses[-1,]
# removal of row.names/numbering
row.names(hypotheses) <- NULL
#correct types
hypotheses$hypothesis <- as.numeric(hypotheses$hypothesis)
hypotheses$Nmin_expanded_in <- as.numeric(hypotheses$Nmin_expanded_in)
hypotheses$Nmin_compared_to <- as.numeric(hypotheses$Nmin_compared_to)
hypotheses$min_expansion_factor <- as.numeric(hypotheses$min_expansion_factor)



#create hypotheses object
# each object has list of exp. OGs
#iterate over list of hyptheses and associate expansions, fasta, msa and trees


#first goal - hypothesis object with hypothesis and all exp.HOGs

#could do it over objects in tea directory
#list.files(path = "tea", pattern = "*", full.names=FALSE)


#alternatively via parsing of hyptheses.tsv
hypotheses$hypothesis


## define three classes
# class for the expanded_OG - containing all different types of data we have on it
setClass("expanded_OG", slots=list(genes="spec_tbl_df",
                                   blast_table="tbl_df",
                                   num_genes_HOG="numeric",
                                   num_genes_extend="numeric",
                                   num_genes_complete="numeric",
                                   genes_HOG="tbl_df",
                                   genes_extend_hits="tbl_df",
                                   fasta_files="list", 
                                   msa="AAStringSet", 
                                   tree="phylo"))


# class for the hypotheses
# adding a prototype is essential here for ortho_intersect_plot since gg has to be defined as 
# register an old-style S3 class using setOldClass
#https://stackoverflow.com/questions/12636056/why-sometimes-i-cant-set-a-class-definition-as-slot-in-a-s4-class
#https://stackoverflow.com/questions/13841400/use-s3-virtual-class-as-slot-of-an-s4-class-got-error-got-class-s4-should-b
#had trouble getting this to work; thus solved differently
# -> seperate list object "Ortho_intersect_plots" hypothesis specific access via index
setClass("hypothesis", 
#         prototype=prototype(ortho_intersect_plot=structure(list(), class="gList")),
         slots=list(description="character", 
                                  number="character",
                                  expanded_in ="character", 
                                  compared_to="character", 
                                  expanded_OGs="list",
                                  species_tree="phylo"))
#                                  ortho_intersect_plot="gg"))

# class for extended BLAST hits info
setClass("extended_BLAST_hits", 
         slots=list(blast_table="tbl_df",
                    num_genes_HOG="numeric",
                    num_genes_extend="numeric",
                    num_genes_complete="numeric",
                    genes_HOG="tbl_df",
                    genes_extend_hits="tbl_df")
         )


rm(t)
rm(hypothesis_1)
rm(hypothesis_2)
rm(HYPOTHESES.a2tea)


#remove protein_names in the snakemake pipeline - directories clean enough


for (hypothesis in hypotheses$hypothesis) {
    # read-in extended_BLAST_hits.RDS object of hypothesis
    extended_BLAST_hits <- readRDS(paste0("tea/", hypothesis, "/extended_BLAST_hits/extended_BLAST_hits.RDS"))
    
    # print(paste0("hypothesis_", hypo))
    
    # create empty list object for hypothesis #
    assign(paste0("hypothesis_", hypothesis), list())

    # assign list of names
    expanded_OGs <- list.files(path = paste0("tea/", hypothesis, "/exp_OGs_proteinnames/"), 
                               pattern = "*", 
                               full.names=FALSE)
    expanded_OGs_short <- str_sub(expanded_OGs, end=-5)

    # assign or subset the orthofinder species_tree based on the current hypothesis
    speciesTree <- ape::keep.tip(read.tree("orthofinder/final-results/Species_Tree/SpeciesTree_rooted_node_labels.txt"), 
                                 c(unlist(str_split(hypotheses$expanded_in[hypothesis], ";")), 
                                   unlist(str_split(hypotheses$compared_to[hypothesis], ";"))))
    
    
    #create empty list
    t <- list()

    for (exp_OG in expanded_OGs_short) {
    # print(exp_OG)
        test <- new("expanded_OG", 
             genes=read_table(paste0("tea/", hypothesis, "/exp_OGs_proteinnames/", exp_OG, ".txt"), col_names = FALSE),
             blast_table=extended_BLAST_hits[[exp_OG]]@blast_table,
             num_genes_HOG=extended_BLAST_hits[[exp_OG]]@num_genes_HOG,
             num_genes_extend=extended_BLAST_hits[[exp_OG]]@num_genes_extend,
             num_genes_complete=extended_BLAST_hits[[exp_OG]]@num_genes_complete,
             genes_HOG=extended_BLAST_hits[[exp_OG]]@genes_HOG,
             genes_extend_hits=extended_BLAST_hits[[exp_OG]]@genes_extend_hits,
             fasta_files=read.fasta(paste0("tea/", hypothesis, "/fa_records/", exp_OG,".fa"), seqtype = "AA", as.string = TRUE), 
             msa=readAAStringSet(paste0("tea/", hypothesis, "/muscle/", exp_OG, ".afa")), 
             tree=read.tree(paste0("tea/", hypothesis, "/trees/", exp_OG, ".tree")))
   
        x <- list(test)
        names(x) <- paste0(exp_OG)
        t <- c(t, x)
    }
 
    # create for each hypothesis a complete hypothesis object with correct naming
    # order: hypothesis@info (name, number, expand, compared, exp OGs)$indiv. exp_OGs@objects (exp.OG list, fa, msa, tree)
    # "expanded_in" and "compared_to" are split on ";" in case their size is > 1
    assign(paste0("hypothesis_", hypothesis),
              new("hypothesis", 
                  description=hypotheses$name[hypothesis],
                  number=as.character(hypothesis),
                  expanded_in=unlist(str_split(hypotheses$expanded_in[hypothesis], ";")),
                  compared_to=unlist(str_split(hypotheses$compared_to[hypothesis], ";")), 
                  expanded_OGs=t,
                  species_tree=speciesTree))#,
#                  ortho_intersect_plot=NULL))
}


# create empty list for final complete hypothesis object

#rm

# create name list of all hypotheses
hypotheses_list <- ls(pattern = "hypothesis_")

# create empty list object to completely hold all hypotheses and associated data
HYPOTHESES.a2tea <- list()

for (hypothesis in hypotheses_list) {
    h <- list(get(hypothesis))
    names(h) <- paste0(hypothesis)
    HYPOTHESES.a2tea <- c(HYPOTHESES.a2tea, h)
}

rm(hypothesis_1)
rm(hypothesis_2)


# final object is called:
# HYPOTHESES.a2tea


#add expanded OGs as column
#    add_column(get(paste0("hypothesis_", hypo)), expanded_OGs)
#class(hypothesis_1@expanded_OGs) <- c("expanded_OG", class(hypothesis_1@expanded_OGs))


[1] 1 2 3 4 5

Warning message in rm(t):
“object 't' not found”
Warning message in rm(hypothesis_1):
“object 'hypothesis_1' not found”
Warning message in rm(hypothesis_2):
“object 'hypothesis_2' not found”
Warning message in rm(HYPOTHESES.a2tea):
“object 'HYPOTHESES.a2tea' not found”

── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()


── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols


── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols


── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols

...


── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols


── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols


── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols


── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols


── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  X1 = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols

In [11]:
length(hypotheses$hypothesis)
head(HYPOTHESES.a2tea$hypothesis_2@expanded_OGs$N0.HOG0000004@blast_table)
#HYPOTHESES.a2tea$hypothesis_2@expanded_OGs$N0.HOG0000028@blast_table

[1] 5

ERROR: Error in h(simpleError(msg, call)): error in evaluating the argument 'x' in selecting a method for function 'head': trying to get slot "blast_table" from an object of a basic class ("NULL") with no slots


### HOG level tables -needs to be behind creation of hypotheses, because they are used here

In [365]:
# create hypothesis specfic HOG level file

#find all tibbles -list
#list.files(path = "tea/1/expansion_tibble", pattern = "expansion_tibble.rds", full.names=TRUE)


#length(hypotheses_list)


HOG_level_list <- list()

#for (i in 1:length(hypotheses_list)) {
for (i in 1:length(hypotheses$hypothesis)) {
    assign(paste0("hypothesis_", i, "_expansion_tibble"),
           readRDS(
               list.files(path = paste0("tea/", i, "/expansion_tibble"), 
                      pattern = "expansion_tibble.rds", 
                      full.names=TRUE)
                  )
           )
    # add to list and name list entries according to hypothesis
    hog_level <- list(get(paste0("hypothesis_", i, "_expansion_tibble")))
    names(hog_level) <- paste0("hypothesis_", i)
    HOG_level_list <- c(HOG_level_list, hog_level)
}

#e.g. the following displays the tibble
#hypothesis_2_expansion_tibble

#r
#append "_gene_count" to all species in HOG tables
#get number of significantly regulated genes per HOG (per species and total) 
# -> (hmm perhaps do this once and then merge?)


# get count of species, HOG, significant combination from HOG_DE.a2tea
# reduce it to HOG, species, count
sig_genes_per_species_and_HOG <- HOG_DE.a2tea %>% 
                                     filter(significant == c("yes")) %>%
                                     filter(HOG != c("singleton")) %>%
                                        group_by(HOG, species, significant) %>% 
                                        mutate(count = n()) %>%
                                        ungroup() %>%
                                        select(HOG, species, count) %>%
            # https://www.r-bloggers.com/2018/05/workaround-for-tidyrspread-with-duplicate-row-identifiers/
            # spread error when no indexing for data
                                            group_by(species) %>% 
                                            mutate(grouped_id = row_number()) %>%  
                                            spread(species, count) %>% 
                                            select(-grouped_id) %>%
            # easy workaround for duplicated rows
                                                distinct()%>% 
            # rename species columns containing now the counts of sig. DE genes
                                                    rename_at(vars(-HOG), ~ paste0(., '_sigDE'))
    # and also add a column summing the rowwise sig. DE counts for all species
    total_sigDE <- sig_genes_per_species_and_HOG %>% select(-HOG) %>% rowSums(na.rm = TRUE) 
    sig_genes_per_species_and_HOG <- add_column(sig_genes_per_species_and_HOG, total_sigDE)
    sig_genes_per_species_and_HOG <- sig_genes_per_species_and_HOG  %>%
                                         group_by(HOG) %>%
                                         # mutate all NAs to 0s
                                         mutate_at(vars(-group_cols()), ~replace(., is.na(.), 0)) %>%
                                         # merge rows per HOG - results in one line per HOG
                                         #summarise_all(funs(sum))
                                         summarise_all(list(sum))

# change the zeros back to NAs
    sig_genes_per_species_and_HOG <- sig_genes_per_species_and_HOG  %>%
                                         na_if(0)

#sig_genes_per_species_and_HOG
#total_sigDE
#inner_join(HOG_level_list[[1]], sig_genes_per_species_and_HOG, by = c("HOG"))
#full_join important - better to keep all HOG rows and allow filtering dynamically in the WebAPP itself

for (i in 1:length(HOG_level_list)) {
    HOG_level_list[[i]] <- HOG_level_list[[i]] %>% rename_at(vars(-HOG, -expansion), ~ paste0(., '_total'))
    HOG_level_list[[i]] <- full_join(HOG_level_list[[i]], sig_genes_per_species_and_HOG, by = c("HOG"))
}

str(HOG_level_list)


#head(HOG_level_list)

#df %>% rename_at(vars(-Name, -State), ~ paste0(., '_2017'))


List of 5
 $ hypothesis_1: tibble [20,913 × 9] (S3: tbl_df/tbl/data.frame)
  ..$ HOG                       : chr [1:20913] "N0.HOG0000000" "N0.HOG0000001" "N0.HOG0000002" "N0.HOG0000003" ...
  ..$ Arabidopsis_thaliana_total: num [1:20913] 0 0 1 1 0 118 115 1 0 91 ...
  ..$ Zea_mays_total            : num [1:20913] 421 2 0 140 0 0 0 91 92 0 ...
  ..$ Hordeum_vulgare_total     : num [1:20913] 0 229 1 1 129 0 1 0 0 0 ...
  ..$ expansion                 : chr [1:20913] "no" "no" "no" "no" ...
  ..$ Arabidopsis_thaliana_sigDE: num [1:20913] NA NA NA NA NA 3 1 NA NA 38 ...
  ..$ Hordeum_vulgare_sigDE     : num [1:20913] NA 7 NA NA 2 NA NA NA NA NA ...
  ..$ Zea_mays_sigDE            : num [1:20913] NA NA NA NA NA NA NA NA NA NA ...
  ..$ total_sigDE               : num [1:20913] NA 7 NA NA 2 3 1 NA NA 38 ...
 $ hypothesis_2: tibble [20,913 × 8] (S3: tbl_df/tbl/data.frame)
  ..$ HOG                       : chr [1:20913] "N0.HOG0000000" "N0.HOG0000001" "N0.HOG0000002" "N0.HOG0000003" ...
  ..$

In [ ]:
summary(HYPOTHESES.a2tea)

In [55]:
HOG_level_list$hypothesis_1
HOG_level_list$hypothesis_1 %>%
    filter(HOG == "N0.HOG0000318")

#HOG_level_list$hypothesis_1 %>% group_by(HOG) %>% summarise(sum(total_sigDE))

HOG           Arabidopsis_thaliana_total Zea_mays_total
1     N0.HOG0000000   0                        421           
2     N0.HOG0000001   0                          2           
3     N0.HOG0000002   1                          0           
4     N0.HOG0000003   1                        140           
5     N0.HOG0000004   0                          0           
6     N0.HOG0000005 118                          0           
7     N0.HOG0000006 115                          0           
8     N0.HOG0000007   1                         91           
9     N0.HOG0000008   0                         92           
10    N0.HOG0000009  91                          0           
11    N0.HOG0000010   0                         89           
12    N0.HOG0000011  81                          0           
13    N0.HOG0000012   0                          0           
14    N0.HOG0000013   1                          1           
15    N0.HOG0000014   1                         74           
16    N0.HOG0000015   0                          1           
17    N0.HOG0000016   0                         78           
18    N0.HOG0000017  75                          0           
19    N0.HOG0000018  71                          0           
20    N0.HOG0000019   0                          0           
21    N0.HOG0000020   0                         69           
22    N0.HOG0000021   0                          0           
23    N0.HOG0000022   0                         65           
24    N0.HOG0000023   1                         61           
25    N0.HOG0000024   0                          0           
26    N0.HOG0000025  59                          0           
27    N0.HOG0000026   0                         58           
28    N0.HOG0000027   2                          1           
29    N0.HOG0000028   1                         12           
30    N0.HOG0000029   0                          0           
⋮     ⋮             ⋮                          ⋮             
20884 N0.HOG0020883 0                          2             
20885 N0.HOG0020884 0                          2             
20886 N0.HOG0020885 0                          2             
20887 N0.HOG0020886 0                          2             
20888 N0.HOG0020887 0                          2             
20889 N0.HOG0020888 0                          2             
20890 N0.HOG0020889 0                          2             
20891 N0.HOG0020890 0                          2             
20892 N0.HOG0020891 0                          2             
20893 N0.HOG0020892 0                          2             
20894 N0.HOG0020893 0                          2             
20895 N0.HOG0020894 0                          2             
20896 N0.HOG0020895 0                          2             
20897 N0.HOG0020896 0                          2             
20898 N0.HOG0020897 0                          2             
20899 N0.HOG0020898 0                          2             
20900 N0.HOG0020899 0                          2             
20901 N0.HOG0020900 0                          2             
20902 N0.HOG0020901 0                          2             
20903 N0.HOG0020902 0                          2             
20904 N0.HOG0020903 0                          2             
20905 N0.HOG0020904 0                          2             
20906 N0.HOG0020905 0                          2             
20907 N0.HOG0020906 0                          2             
20908 N0.HOG0020907 0                          2             
20909 N0.HOG0020908 0                          2             
20910 N0.HOG0020909 0                          2             
20911 N0.HOG0020910 0                          2             
20912 N0.HOG0020911 0                          2             
20913 N0.HOG0020912 0                          2             
      Hordeum_vulgare_total expansion Arabidopsis_thaliana_sigDE
1       0                   no        NA                        
2     229                   no  

HOG           Arabidopsis_thaliana_total Zea_mays_total Hordeum_vulgare_total
1 N0.HOG0000318 15                         0              0                    
  expansion Arabidopsis_thaliana_sigDE Hordeum_vulgare_sigDE Zea_mays_sigDE
1 no        1                          NA                    NA            
  total_sigDE
1 1

### checking for sigDE mistakes - where does this in the first row come from?

In [172]:
#checking for sigDE mistakes - where does this in the first row come from?
HOG_level_list[[2]] %>%
  rowwise() %>%
  filter(Hordeum_vulgare_total < Hordeum_vulgare_sigDE) %>%
  head()

HOG           Hordeum_vulgare_total Zea_mays_total expansion
1 N0.HOG0002277 3                     3              no       
  Arabidopsis_thaliana_sigDE Hordeum_vulgare_sigDE Zea_mays_sigDE total_sigDE
1 NA                         6                     1              7          
  norm_sum_expanded_sigDE norm_sum_compared_sigDE norm_phyper
1 6                       1                       0.8632795

### Calculating enrichment of sig. diff. exp. genes of expanded_in species per HOG

In [366]:
#install.packages("stringr")
library(stringr)

# what variables do I need?
#expanded_in = 
#compared_to =

#if no ";" (only one species)
#str_split(hh_expanded_in, ";")
#str_split(hh_compared_to, ";")

## respective length -> amount of species per category (since I need to divide/normalize by this)
#-> so n expanded_in species
#-> and n compared_to species

## use mutate to add new columns for normalized
#total number of sig. diff. genes - expanded_in species  /(divided by) n expanded_in species
#total number of sig. diff. genes - compared_to species  /(divided by) n compared_to species


#everything handled here
for (i in 1:length(hypotheses$hypothesis)) {
    h_expanded_in <- unlist(str_split(hypotheses$expanded_in[i], ";"))
    h_compared_to <- unlist(str_split(hypotheses$compared_to[i], ";"))
    length_expanded_in <- length(h_expanded_in)
    length_compared_to <- length(h_compared_to)
    
    HOG_level_list[[i]] <- HOG_level_list[[i]] %>%
      mutate(
        norm_sum_expanded_sigDE = rowSums(select(., paste0(h_expanded_in, "_sigDE")), na.rm=TRUE) / length_expanded_in
      )
    
    HOG_level_list[[i]] <- HOG_level_list[[i]] %>%
      mutate(
        norm_sum_compared_sigDE = rowSums(select(., paste0(h_compared_to, "_sigDE")), na.rm=TRUE) / length_compared_to
      )
      
    #compute column sums for norm_expanded_minus_compared_sigDE and norm_sum_all_nonsig
    #only sum positive values of norm_expanded_minus_compared_sigDE
    sum_white <- HOG_level_list[[i]] %>% 
      summarise(summed = sum(norm_sum_expanded_sigDE)) %>%
      pull()
    
    sum_black <- HOG_level_list[[i]] %>% 
      summarise(summed = sum(norm_sum_compared_sigDE)) %>%
      pull()
    
    
    #calculate 
    HOG_level_list[[i]] <- HOG_level_list[[i]] %>%
      rowwise() %>%
       mutate(
        oaes_hyper = phyper(norm_sum_expanded_sigDE - 1, 
                             sum_white, 
                             sum_black, 
                             norm_sum_expanded_sigDE + norm_sum_compared_sigDE, 
                             lower.tail = FALSE)
        ) %>% ungroup() %>%
       
      mutate(
        oaes_hyper = case_when(
                        oaes_hyper == 1 ~ NA_real_,
                        TRUE ~ oaes_hyper
                   )
      )

}
 

### OLD IDEAS
#total number of NON sig. diff. genes - expanded_in species  /(divided by) n expanded_in species
#total number of NON sig. diff. genes - compared_to species  /(divided by) n compared_to species

#finally a column of normalized total n genes per HOG
#-> sum of this column constitutes the normalized amount of all genes in all HOGs

#once we have these numbers we perform a multivariate hypergeomteric test
    
    #    HOG_level_list[[i]] <- HOG_level_list[[i]] %>%
#      mutate(
#        norm_sum_expanded_nonsig = (rowSums(select(., paste0(h_expanded_in, "_total")), na.rm=TRUE) / length_expanded_in) - (rowSums(select(., paste0(h_expanded_in, "_sigDE")), na.rm=TRUE) / length_expanded_in)
#      )
    
#    HOG_level_list[[i]] <- HOG_level_list[[i]] %>%
#      mutate(
#        norm_sum_compared_nonsig = (rowSums(select(., paste0(h_compared_to, "_total")), na.rm=TRUE) / length_compared_to) - (rowSums(select(., paste0(h_compared_to, "_sigDE")), na.rm=TRUE) / length_compared_to)
#      )

#    HOG_level_list[[i]] <- HOG_level_list[[i]] %>%
#      mutate(
#        norm_expanded_minus_compared_sigDE = norm_sum_expanded_sigDE - norm_sum_compared_sigDE
#      )
    
#    HOG_level_list[[i]] <- HOG_level_list[[i]] %>%
##      rowwise() %>%
#      mutate(
#        norm_sum_all_nonsig = rowSums(select(., "norm_sum_expanded_nonsig", "norm_sum_compared_nonsig"), na.rm=TRUE) / length_compared_to
#      )
    
    #perform phyper test - in cases where (expanded-compared) yields negative values will just default to 1
#    HOG_level_list[[i]] <- HOG_level_list[[i]] %>%
#      rowwise() %>%
#       mutate(
#        norm_phyper = phyper(
#                norm_expanded_minus_compared_sigDE, 
#                sum_white, 
#                sum_black, 
#                norm_sum_compared_nonsig, 
#                lower.tail = FALSE)
#         nom_phyper =  phyper(3, sum_white, sum_black, 5, lower.tail = FALSE)

#        )
    
#    HOG_level_list[[i]] <- HOG_level_list[[i]] %>%
#      mutate(
#        norm_sum = rowSums(
#                               select(.,
#                                      "norm_expanded_minus_compared_sigDE",  
#                                      "norm_sum_expanded_nonsig", 
#                                      "norm_sum_compared_nonsig"
#                                     ),
#                                na.rm=TRUE)
#      )

In [176]:
#phyper exploration
a = 14
b = 11832
c = 1238
d = 0

e = a + d


phyper(a-1,b,c,e, lower.tail = FALSE)

[1] 0.2481072

### adding the computed cafe p-values to the HOG_level tables

In [367]:
for (hypothesis_num in 1:length(HOG_level_list)) {

  cafe_tibble <- read_tsv(paste0("cafe/", hypothesis_num, "/cafe_complete_results/Gamma_family_results.txt"))[1:2]

  HOG_level_list[[hypothesis_num]] <- HOG_level_list[[hypothesis_num]] %>%
                                        left_join(., 
                                                  cafe_tibble, 
                                                  by = c("HOG" = "#FamilyID")
                                                 ) %>%
                                        rename(cafe_pvalue = pvalue) %>%
                                        relocate(cafe_pvalue, .after = oaes_hyper) %>%
                                        arrange(oaes_hyper)
}


── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  `#FamilyID` = col_character(),
  pvalue = col_double(),
  `Significant at 0.05` = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  `#FamilyID` = col_character(),
  pvalue = col_double(),
  `Significant at 0.05` = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  `#FamilyID` = col_character(),
  pvalue = col_double(),
  `Significant at 0.05` = col_character()
)



── Column specification ────────────────────────────────────────────────────────────────────────────────────────
cols(
  `#FamilyID` = col_character(),
  pvalue = col_double(),
  `Significant at 0.05` = col_character()
)



── Column specification ───────────────────────────────────────────────────────────────────────────────

In [368]:
#cafe only outputs p-values until 0.001 - so I will as a quick hack change all 0s to 0.001
#perhaps I can modify the C++ code of CAFE5 a bit so I get longer doubles?
#on the other hand this is probably not really necessary
for (hypothesis_num in 1:length(HOG_level_list)) {

  HOG_level_list[[hypothesis_num]] <- HOG_level_list[[hypothesis_num]] %>%
    mutate(
      cafe_pvalue = case_when(
                      cafe_pvalue == 0 ~ 0.001,
                      TRUE ~ cafe_pvalue
                   )
    )
}

In [312]:
HOG_level_list[[4]] %>% filter(expansion == "yes") %>% tail(n=20)

HOG           Hordeum_vulgare_total Zea_mays_total
1  N0.HOG0013346 0                     2             
2  N0.HOG0013365 0                     2             
3  N0.HOG0013416 0                     2             
4  N0.HOG0013446 0                     2             
5  N0.HOG0013447 0                     2             
6  N0.HOG0013480 0                     2             
7  N0.HOG0013511 0                     2             
8  N0.HOG0013529 0                     2             
9  N0.HOG0013564 0                     2             
10 N0.HOG0013603 2                     0             
11 N0.HOG0013611 0                     2             
12 N0.HOG0013622 0                     2             
13 N0.HOG0013661 0                     2             
14 N0.HOG0013666 0                     2             
15 N0.HOG0013670 2                     0             
16 N0.HOG0013685 0                     2             
17 N0.HOG0013794 0                     2             
18 N0.HOG0013797 0                     2             
19 N0.HOG0013801 0                     2             
20 N0.HOG0013828 0                     2             
   Arabidopsis_thaliana_total expansion Arabidopsis_thaliana_sigDE
1  1                          yes       NA                        
2  1                          yes        1                        
3  1                          yes       NA                        
4  1                          yes       NA                        
5  1                          yes       NA                        
6  1                          yes       NA                        
7  1                          yes       NA                        
8  1                          yes       NA                        
9  1                          yes       NA                        
10 1                          yes       NA                        
11 1                          yes       NA                        
12 1                          yes        1                        
13 1                          yes        1                        
14 1                          yes        1                        
15 1                          yes       NA                        
16 1                          yes       NA                        
17 1                          yes       NA                        
18 1                          yes       NA                        
19 1                          yes        1                        
20 1                          yes       NA                        
   Hordeum_vulgare_sigDE Zea_mays_sigDE total_sigDE norm_sum_expanded_sigDE
1  NA                     1              1          0.5                    
2  NA                     1              2          0.5                    
3  NA                    NA             NA          0.0                    
4  NA                    NA             NA          0.0                    
5  NA                    NA             NA          0.0                    
6  NA                     1              1          0.5                    
7  NA                    NA             NA          0.0                    
8  NA                    NA             NA          0.0                    
9  NA                    NA             NA          0.0                    
10  1                    NA              1          0.5                    
11 NA                    NA             NA          0.0                    
12 NA                    NA              1          0.0                    
13 NA                    NA              1          0.0                    
14 NA                     1              2          0.5                    
15 NA                    NA             NA          0.0                    
16 NA                    NA             NA          0.0                    
17 NA                    NA             NA          0.0                    
18 NA                    NA             NA          0.0                    
19 NA             

### combine overrep. analysis of sig. exp. genes with cafe value of gene expansion

In [188]:
#install.packages("poolr")
#library(poolr)

#poolr::fisher(c(0.2, 0.05))
#>combined p-values with:      Fisher's method
#>number of p-values combined: 2 
#>test statistic:              9.21 ~ chi-square(df = 4) 
#>adjustment:                  none 
#>combined p-value:            0.0560517

#result can be accessed via $p

#poolr seems like the better suited package overall (alternatives to simple fisher's method),
#but sadly it's not installable via conda yet - thus kept here as a reminder

# for now survcomp's combine.test will have to make do
#if (!requireNamespace("BiocManager", quietly = TRUE))
#    install.packages("BiocManager")
#BiocManager::install("survcomp")
library(survcomp)
#combine.test(c(0.2, 0.05))
#>0.0560517018598809

In [382]:
for (i in 1:length(hypotheses$hypothesis)) {
 
    #calculate the tea-value - trait-associated evolutionary adaption value
    HOG_level_list[[i]] <- HOG_level_list[[i]] %>%
      rowwise() %>%
      mutate(
        tea_value = case_when(
                      is.na(oaes_hyper) ~ NA_real_,
                      is.na(cafe_pvalue) ~ NA_real_,
                      is.na(oaes_hyper) & is.na(cafe_pvalue) ~ NA_real_,
                      TRUE ~ 1 # don't really get why I can't do it here:
                               # combine.test(c(oaes_hyper, cafe_pvalue), na.rm = TRUE)
                    )          # results in error as soon as both elements are NA
                               # seems like case_when calls everything anyways, even though the previous cases
                               # should make it skip the line..; anyways quick workaround with second mutate()
      ) %>%
      mutate(
        tea_value = case_when(
                      tea_value == 1 ~ combine.test(c(oaes_hyper, cafe_pvalue), na.rm = TRUE)
                    )
      ) %>%
      ungroup() %>%
      arrange(tea_value) 
}

In [360]:
#?combine.test
typeof(
combine.test(c(NA, NA), na.rm = TRUE)
    )

[1] 0.9994098

In [383]:
HOG_level_list[[1]][1:25,] #%>% arrange(oaes_hyper) %>% head()

HOG           Arabidopsis_thaliana_total Zea_mays_total
1  N0.HOG0000066  35                         0            
2  N0.HOG0000133  22                         0            
3  N0.HOG0000208  16                         0            
4  N0.HOG0000560  11                         1            
5  N0.HOG0000470  12                         0            
6  N0.HOG0000737  10                         1            
7  N0.HOG0000368  13                         1            
8  N0.HOG0000859   9                         0            
9  N0.HOG0000017  75                         0            
10 N0.HOG0000056  37                         1            
11 N0.HOG0000176   2                        16            
12 N0.HOG0000535  11                         0            
13 N0.HOG0000614   2                         9            
14 N0.HOG0000018  71                         0            
15 N0.HOG0000236  12                         1            
16 N0.HOG0001537   7                         1            
17 N0.HOG0000006 115                         0            
18 N0.HOG0000377  12                         1            
19 N0.HOG0000399   1                        11            
20 N0.HOG0000401   1                        12            
21 N0.HOG0000445  11                         1            
22 N0.HOG0000534   2                        10            
23 N0.HOG0000538   1                        10            
24 N0.HOG0000998   1                         8            
25 N0.HOG0001287   1                         8            
   Hordeum_vulgare_total expansion Arabidopsis_thaliana_sigDE
1  1                     no        18                        
2  1                     no         7                        
3  2                     no         6                        
4  0                     no         6                        
5  1                     no         5                        
6  0                     no         4                        
7  0                     no         3                        
8  1                     no         3                        
9  2                     no         2                        
10 0                     no         2                        
11 2                     no         2                        
12 1                     no         2                        
13 1                     no         2                        
14 1                     no         3                        
15 4                     yes        3                        
16 0                     no         3                        
17 1                     no         1                        
18 1                     yes        1                        
19 2                     no         1                        
20 1                     no         1                        
21 1                     yes        1                        
22 0                     no         1                        
23 1                     no         1                        
24 1                     no         1                        
25 0                     no         1                        
   Hordeum_vulgare_sigDE Zea_mays_sigDE total_sigDE norm_sum_expanded_sigDE
1   1                    NA             19          18                     
2  NA                    NA              7           7                     
3   1                    NA              7           6                     
4  NA                    NA              6           6                     
5  NA                    NA              5           5                     
6  NA                    NA              4           4                     
7  NA                    NA              3           3                     
8  NA                    NA              3           3                     
9  NA                    NA              2           2                     
10 NA                    NA              2           2                     
11 NA                

In [385]:
HOG_level_list[[2]] %>% filter(expansion=="yes") %>% arrange(tea_value) %>% head(n=10)

HOG           Hordeum_vulgare_total Zea_mays_total expansion
1  N0.HOG0000063 35                    2              yes      
2  N0.HOG0000074 33                    1              yes      
3  N0.HOG0000081 32                    1              yes      
4  N0.HOG0000044 41                    3              yes      
5  N0.HOG0000527 12                    1              yes      
6  N0.HOG0000047 31                    8              yes      
7  N0.HOG0000049 37                    4              yes      
8  N0.HOG0000075 31                    3              yes      
9  N0.HOG0000220 17                    1              yes      
10 N0.HOG0000080 32                    1              yes      
   Arabidopsis_thaliana_sigDE Hordeum_vulgare_sigDE Zea_mays_sigDE total_sigDE
1  NA                         14                    NA             14         
2  NA                         14                    NA             14         
3  NA                         12                    NA             12         
4  NA                         11                    NA             11         
5  NA                         11                    NA             11         
6   1                         10                    NA             11         
7  NA                          9                    NA              9         
8  NA                          9                    NA              9         
9  NA                          9                    NA              9         
10 NA                          8                    NA              8         
   norm_sum_expanded_sigDE norm_sum_compared_sigDE oaes_hyper cafe_pvalue
1  14                      0                       0.2481072  0.001      
2  14                      0                       0.2481072  0.001      
3  12                      0                       0.3028038  0.001      
4  11                      0                       0.3345161  0.001      
5  11                      0                       0.3345161  0.001      
6  10                      0                       0.3695466  0.001      
7   9                      0                       0.4082422  0.001      
8   9                      0                       0.4082422  0.001      
9   9                      0                       0.4082422  0.001      
10  8                      0                       0.4509861  0.001      
   tea_value  
1  0.002307806
2  0.002307806
3  0.002756249
4  0.003011590
5  0.003011590
6  0.003290160
7  0.003594022
8  0.003594022
9  0.003594022
10 0.003925417

In [245]:
hypotheses

hypothesis name                                        
1 1          Expanded in Arabidopsis compared to Monocots
2 2          Expanded in barley compared to maize        
3 3          bla                                         
4 4          bla2                                        
5 5          bla3                                        
  expanded_in              compared_to                         
1 Arabidopsis_thaliana     Zea_mays;Hordeum_vulgare            
2 Hordeum_vulgare          Zea_mays                            
3 Zea_mays                 Hordeum_vulgare;Arabidopsis_thaliana
4 Hordeum_vulgare;Zea_mays Arabidopsis_thaliana                
5 Hordeum_vulgare;Zea_mays Hordeum_vulgare;Arabidopsis_thaliana
  Nmin_expanded_in Nmin_compared_to min_expansion_factor expanded_in_all_found
1 1                2                2                    YES                  
2 1                1                2                    NO                   
3 1                1                3                    YES                  
4 1                1                2                    NO                   
5 1                1                2                    NO                   
  compared_to_all_found
1 YES                  
2 NO                   
3 YES                  
4 NO                   
5 NO

### Last step: saving everything to one file which is input for the A2TEA WebApp

In [ ]:
save(hypotheses, 
     HYPOTHESES.a2tea, 
     HOG_DE.a2tea, 
     HOG_level_list, 
#     Ortho_intersect_plots,
     file = "tea/A2TEA_finished.RData")

# To load the data again
#load("tea/A2TEA_finished.RData")

#perhaps use this to name output based on time?
#paste0("tea/A2TEA_finished_",
#    str_replace_all(
#    str_replace_all(
#        Sys.time(), ":", "-"),
#    " ", "_"
#                    ), ".RData")

In [ ]:
load("tea/A2TEA_finished.RData")

In [ ]:
HOG_level_list$hypothesis_2

In [ ]:
HYPOTHESES.a2tea$hypothesis_1@expanded_OGs$N0.HOG0000207@blast_table

## Old ideas & approaches

### computation of tea value (first idea)

expansion ratio (exp/com) (9/4) x expression ratio (com/exp) (2/6) 
---- don't need (n_species_expanded/n_species_compared); stays equal in a hypothesis; similar to p-values not          comparable between different experiments
divided by HOG size (all genes in HOG for this particular hypothesis) x number of significantly regulated genes


problem - how to deal with missing values???

In [ ]:
# should I only have hypothesis species (total count and sigDE) HOG_level_list tables?

#new column tea-value
#if expansion yes continue; else NA value
#because we set expansion as criterium, species gene count has to be >=1
#sig DE counts can be NA ! - we could just add a pseudocount of 1 at these positions for the calculation

#so per line that has expansion = yes:
#get all expanded species; sum their gene counts; sum their sigDE counts
#get all compared species; sum their gene counts; sum their sigDE counts
#expansion_ratio <- divide summed gene count expanded by summed gene count compared
#expression_ratio <- divide summed SigDE count expanded by summed SigDE count compared
#e2_ratio <- divide expansion_ratio by expression_ratio
#tea-value <- divide e2_ratio by total number of genes in HOG and then by total number of SigDE in HOG


# outer most loop; going through hypotheses in HOG_level_list
for (i in 1:length(HOG_level_list)) {
    
    # access the names of all species important for the hypothesis - expanded_in; compared_to
    print(c(unlist(str_split(HYPOTHESES.a2tea[[i]]@expanded_in, ";")), 
            unlist(str_split(HYPOTHESES.a2tea[[i]]@compared_to, ";"))))
    
    # creating a relevant species vector might make this more future proof;
    # since I might change the completeness of the HOG_level_list elements
#    relevant_species <- c(unlist(str_split(HYPOTHESES.a2tea[[i]]@expanded_in, ";")), 
#                          unlist(str_split(HYPOTHESES.a2tea[[i]]@compared_to, ";")))
    
    expanded_species <- unlist(str_split(HYPOTHESES.a2tea[[i]]@expanded_in, ";"))
    
    compared_species <- unlist(str_split(HYPOTHESES.a2tea[[i]]@compared_to, ";"))                              
                                  
    ## pre-allocate empty vector for tea value with length of nrow of current hypothesis of HOG_level_list
    # neat; because NAs already in there so I can just skip if the HOG shows no expansion ;D
    tea_value <- rep(NA, nrow(HOG_level_list[[i]]))
    
    
    ## create "geneCount_workset" containing HOGs and counts of all relevant species
    geneCount_workset <-  HOG_level_list[[i]]

    # create geneCount_EXP_workset & geneCount_COMP_workset + drop columns that are unnecessary                  
    geneCount_EXP_workset <- geneCount_workset %>% 
                             select(ends_with("_total")) %>%
                             select(contains(expanded_species))
                        # also remove the "_total" ending
    geneCount_EXP_workset <- geneCount_EXP_workset %>% 
                             setNames(names(geneCount_EXP_workset) %>% 
                             stringr::str_replace("_total",""))
                          
    geneCount_COMP_workset <- geneCount_workset %>% 
                             select(ends_with("_total")) %>%
                             select(contains(compared_species))
                        # also remove the "_total" ending
    geneCount_COMP_workset <- geneCount_COMP_workset %>% 
                             setNames(names(geneCount_COMP_workset) %>% 
                             stringr::str_replace("_total",""))
                    

    ## create "geneSig_workset" containing HOGs and counts of all relevant species 
    geneSig_workset <-  HOG_level_list[[i]]
    
    # create geneSig_EXP_workset & geneSig_COMP_workset + drop columns that are unnecessary                  
    geneSig_EXP_workset <- geneSig_workset %>% 
                             select(ends_with("_sigDE")) %>%
                             select(contains(expanded_species))
                        # also remove the "_sigDE" ending
    geneSig_EXP_workset <- geneSig_EXP_workset %>% 
                             setNames(names(geneSig_EXP_workset) %>% 
                             stringr::str_replace("_sigDE",""))
                          
    geneSig_COMP_workset <- geneSig_workset %>% 
                             select(ends_with("_sigDE")) %>%
                             select(contains(compared_species))
                        # also remove the "_sigDE" ending
    geneSig_COMP_workset <- geneSig_COMP_workset %>% 
                             setNames(names(geneSig_COMP_workset) %>% 
                             stringr::str_replace("_sigDE",""))

                               
    # nested loop that goes through current hypothesis HOG_level_list line by line
    for (j in 1:nrow(HOG_level_list[[i]])) {
        # write value into index slot if current HOG does pass hard filter expansion criterium
        # if expansion == "no" do nothing; since we prefilled all positions with NA
        if (HOG_level_list[[i]][j,"expansion"] == "yes") {
            
            ## compute all the different sub-values for the tea_value
            # count of all genes in expanded species in HOG
            geneCount_EXP_HOG <- geneCount_EXP_workset[j,] %>%
                                 dplyr::rowwise() %>%
                                 sum()
            
            # count of all genes in compared species in HOG
            geneCount_COMP_HOG <- geneCount_COMP_workset[j,] %>%
                                      dplyr::rowwise() %>%
                                      sum()
            
            # sum genes of expanded & compared species in HOG
            geneCount_BOTH_HOG <- sum(geneCount_EXP_HOG, geneCount_COMP_HOG)
            
            
            # count of all sig DE genes in expanded species in HOG
            geneSig_EXP_HOG <- geneSig_EXP_workset[j,] %>%
                                 dplyr::rowwise() %>%
                                 sum()
            
            # count of all sig DE genes in compared species in HOG
            geneSig_COMP_HOG <- geneSig_COMP_workset[j,] %>%
                                      dplyr::rowwise() %>%
                                      sum()
            
            ## sigDE columns can contain zero (NA in table) counts
            ## we exchange this for a pseudocount 1
            ## doesn't impact tea_value too much
            if (is.na(geneSig_EXP_HOG)) {
                geneSig_EXP_HOG <- 1
            }
            
            if (is.na(geneSig_COMP_HOG)) {
                geneSig_COMP_HOG <- 1
            }
            
            # sum Sig DE genes of expanded & compared species in HOG
            geneSig_BOTH_HOG <- sum(geneSig_EXP_HOG, geneSig_COMP_HOG)

            
            ## perform tea value calculation
            int_tea_value <- (geneCount_EXP_HOG / geneCount_COMP_HOG) * (geneSig_COMP_HOG / geneSig_EXP_HOG) / 
                                                  (geneCount_BOTH_HOG * geneSig_BOTH_HOG)
            
            # lastly, add computed value to tea_value at index of current j loop position
            tea_value[j] <- int_tea_value
        }
    }
    
    ## add tea_value as new column to HOG_level_list table
    HOG_level_list[[i]] <- HOG_level_list[[i]] %>% 
                               add_column(tea_value, .after = "HOG")
    
}

### creating Venn (or alternative diagrammes for the hypothesis)
### -> will be moved to the WebApp and computed there...

In [ ]:
# create this awesome function to change area of plotting
# https://stackoverflow.com/questions/1279003/specify-width-and-height-of-plot
set_plot_dimensions <- function(width_choice, height_choice) {
        options(repr.plot.width=width_choice, repr.plot.height=height_choice)
        }
# use funtion to set area a bit wider
set_plot_dimensions(32, 10)



#step 1: removing all species not in hypothesis or keep only those that are
# using HOG_level_list and looking at the "_total" columns
#  only species in this hypothesis are in here ;D
# -> still drop all columns not necessary?
#step 2: perform check on size of this set
# -> if < 5 then create Venn diagramme
# -> if > 5 then create alternative plot
# create plot and safe as sub element in HYPOTHESES.a2tea object 



#HOG_DE.a2tea
#HOG_level_list[[1]]
#choose based on set length 2,3,4,5 after that UpsetR


Ortho_intersect_plots <- list()

for (i in 1:length(HOG_level_list)) {

workset <-  HOG_level_list[[i]]
# drop columns that are unnecessary
workset <- workset %>% select(HOG, ends_with("_total")) 
# add this point we can easily compute the number of species/ecotypes etc. 
# #species = (columns of current workset - 1) 
species_num <- ncol(workset) - 1
# change 0 to NAs since we can more easily filter on that
is.na(workset) <- workset==0
# remove '_total' from column names
#str_remove(colnames(workset), "_total")
workset <- workset %>% setNames(names(workset) %>% stringr::str_replace("_total",""))

# for testing purposes - remove Genotype vectors
rm(Genotype1,Genotype2,Genotype3)

genotypeList <- list()
for (j in 1:species_num) {
    assign(paste0("Genotype", j), as.vector(simplify_all(workset[!is.na(workset[j+1]),"HOG"])[[1]]))
    subList <- list(get(paste0("Genotype", j)))
    names(subList) <- colnames(workset)[j+1]
    genotypeList <- c(genotypeList, subList)
}


#using UpSetR
upsetOrtho <- upset(fromList(genotypeList), 
                   order.by = "freq",
                   empty.intersections = "on",
                   point.size = 3.5, 
                   line.size = 2, 
                   mainbar.y.label = "HOG Intersections", 
                   text.scale = c(2, 1.3, 1, 1, 2, 2))

p <- upsetOrtho

# if we have less than 5 species draw a venn diagramme
# combine both plots with some trickery
if (species_num < 5) {
    
# draw venn diagramme
orthoVenn <- venn.diagram(genotypeList,
                           print.mode = c("raw","percent"),
                           sigdigs = 1,
                           filename = NULL,
                           category = names(genotypeList),
                           fill = rainbow(length(names(genotypeList))),
                           cat.col = rainbow(length(names(genotypeList))),
                           cat.cex = 2,
                           cex = 1.5,
                           margin = 0.05
                           )    
    
# as.grob from ggplotify is necessary
orthoIntersect <- plot_grid(orthoVenn, 
          as.grob(upsetOrtho), 
          rel_widths = c(1/3, 2/3))

#p <- ggplotify::as.ggplot(orthoIntersect)
p <- orthoIntersect
    }

Ortho_intersect_plots[[i]] <- p

}
    
    
    


In [ ]:
Ortho_intersect_plots[[1]]